# ANN to clssify customer churn

In [1]:
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

In [2]:
dataset=pd.read_csv('/Users/aparajit/Desktop/PROJECTS/Churn_Modelling.csv')

In [3]:
dataset.head()

RowNumber  CustomerId   Surname  CreditScore Geography  Gender  Age  \
0          1    15634602  Hargrave          619    France  Female   42   
1          2    15647311      Hill          608     Spain  Female   41   
2          3    15619304      Onio          502    France  Female   42   
3          4    15701354      Boni          699    France  Female   39   
4          5    15737888  Mitchell          850     Spain  Female   43   

   Tenure    Balance  NumOfProducts  HasCrCard  IsActiveMember  \
0       2       0.00              1          1               1   
1       1   83807.86              1          0               1   
2       8  159660.80              3          1               0   
3       1       0.00              2          0               0   
4       2  125510.82              1          1               1   

   EstimatedSalary  Exited  
0        101348.88       1  
1        112542.58       0  
2        113931.57       1  
3         93826.63       0  
4         79084.10       0

In [4]:
x=dataset.iloc[:,3:13].values

In [5]:
y=dataset.iloc[:,13].values

* Encoding the categorical variables (Country, gender)

In [6]:
from sklearn.preprocessing import LabelEncoder, OneHotEncoder

In [7]:
labelencoder_country=LabelEncoder()

In [8]:
x[:,1]=labelencoder_country.fit_transform(x[:,1])

In [9]:
labelencoder_sex=LabelEncoder()

In [10]:
x[:,2]=labelencoder_sex.fit_transform(x[:,2])

Creating Binary variables for country using onehotencoder 

In [11]:
onehotencoder=OneHotEncoder(categorical_features=[1])

In [12]:
x=onehotencoder.fit_transform(x).toarray()

Removing the first dummy variable 

In [13]:
x=x[:,1:]

* Using 80/20 split on the data to split it into train and test sets 

In [14]:
from sklearn.model_selection import train_test_split

In [15]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.20)

* Centre and scaling the independent variables 

In [16]:
from sklearn.preprocessing import StandardScaler

In [17]:
sc=StandardScaler()

In [18]:
x_train=sc.fit_transform(x_train)

In [19]:
x_test=sc.transform(x_test)

Importing Keras and other required packages

In [20]:
import keras

/Users/aparajit/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


* Sequential module from keras is needed to initialize ANN
* Dense module from keras needed to build the ANN layers 
* We will sequentially define the layers in the ANN to predict class of churn (0,1)

In [21]:
from keras.models import Sequential
from keras.layers import Dense

Now trying to tune the same model using K-fold cross validation and gridsearch to get better accuracy 

* Creating the ANN structure within a fucntion since Kerasclassifier uses a fucntion using the same kernel and activation fucntions and layers as used earlier

* Dropout added to avoid overfitting (p defines the percentage of neurons that should stop firing at random)

# Model build and Parameter Tuning 

In [22]:
from keras.wrappers.scikit_learn import KerasClassifier

In [23]:
from sklearn.model_selection import GridSearchCV

In [24]:
from keras.layers import Dropout

In [25]:
def build_ann(optimizer):
    classifier= Sequential()
    classifier.add(Dense(units=6,kernel_initializer='uniform',activation='relu',input_dim=11))
    classifier.add(Dense(units=6,kernel_initializer='uniform',activation='relu'))
    classifier.add(Dense(units=1,kernel_initializer='uniform',activation='sigmoid'))
    classifier.compile(optimizer=optimizer,loss='binary_crossentropy',metrics=['accuracy'])
    return classifier

In [26]:
classifier=KerasClassifier(build_fn=build_ann)

In [27]:
param={'batch_size':[25,50,100],'epochs':[50,100,500],'optimizer':['adam','rmsprop']}

In [28]:
grid_search=GridSearchCV(estimator=classifier,param_grid=param,scoring='accuracy',cv=10,n_jobs=-1)

In [29]:
grid_search=grid_search.fit(x_train,y_train)

Epoch 1/50
Epoch 1/50
Epoch 1/50
Epoch 1/50
7200/7200 [==============================] - 1s 136us/step - loss: 0.5586 - acc: 0.7932
Epoch 2/50
7200/7200 [==============================] - 1s 142us/step - loss: 0.5555 - acc: 0.7951
Epoch 2/50
7200/7200 [==============================] - 1s 149us/step - loss: 0.5536 - acc: 0.7992
Epoch 2/50
7200/7200 [==============================] - 1s 90us/step - loss: 0.4365 - acc: 0.7974
Epoch 3/50
7200/7200 [==============================] - 1s 81us/step - loss: 0.4314 - acc: 0.7999
Epoch 3/50
7200/7200 [==============================] - 1s 96us/step - loss: 0.4392 - acc: 0.7939
Epoch 3/50
7200/7200 [==============================] - 1s 96us/step - loss: 0.4247 - acc: 0.7999
Epoch 4/50
7200/7200 [==============================] - 1s 96us/step - loss: 0.4304 - acc: 0.7958
Epoch 4/50
7200/7200 [==============================] - 1s 115us/step - loss: 0.4301 - acc: 0.7974
Epoch 4/50
7200/7200 [==============================] - 1s 87us/step - loss: 0.42

7200/7200 [==============================] - 1s 109us/step - loss: 0.4085 - acc: 0.8336
Epoch 19/50


/Users/aparajit/anaconda3/lib/python3.6/site-packages/keras/callbacks.py:120: UserWarning: Method on_batch_end() is slow compared to the batch update (0.119420). Check your callbacks.
  % delta_t_median)


7200/7200 [==============================] - 1s 110us/step - loss: 0.4023 - acc: 0.8382
Epoch 19/50
7200/7200 [==============================] - 1s 86us/step - loss: 0.4080 - acc: 0.8357
Epoch 20/50
7200/7200 [==============================] - 1s 113us/step - loss: 0.4085 - acc: 0.8351
Epoch 20/50
7200/7200 [==============================] - 1s 94us/step - loss: 0.4018 - acc: 0.8389
Epoch 20/50
7200/7200 [==============================] - 1s 85us/step - loss: 0.4078 - acc: 0.8336
Epoch 21/50
7200/7200 [==============================] - 1s 97us/step - loss: 0.4074 - acc: 0.8332
Epoch 21/50
7200/7200 [==============================] - 1s 90us/step - loss: 0.4064 - acc: 0.8374
Epoch 21/50
7200/7200 [==============================] - 1s 90us/step - loss: 0.4077 - acc: 0.8350
Epoch 22/50
7200/7200 [==============================] - 1s 98us/step - loss: 0.4070 - acc: 0.8342
Epoch 22/50
7200/7200 [==============================] - 1s 109us/step - loss: 0.4060 - acc: 0.8385
Epoch 22/50
7200/72

7200/7200 [==============================] - 1s 119us/step - loss: 0.4220 - acc: 0.7954
Epoch 6/50
7200/7200 [==============================] - 1s 123us/step - loss: 0.4223 - acc: 0.7983
Epoch 6/50
7200/7200 [==============================] - 1s 132us/step - loss: 0.4222 - acc: 0.7964
Epoch 6/50
7200/7200 [==============================] - 1s 142us/step - loss: 0.4209 - acc: 0.7981
Epoch 6/50
7200/7200 [==============================] - 1s 132us/step - loss: 0.4199 - acc: 0.8099
Epoch 7/50
7200/7200 [==============================] - 1s 137us/step - loss: 0.4191 - acc: 0.8118
Epoch 7/50
7200/7200 [==============================] - 1s 124us/step - loss: 0.4181 - acc: 0.8104
Epoch 7/50
7200/7200 [==============================] - 1s 126us/step - loss: 0.4182 - acc: 0.8210
Epoch 8/50
7200/7200 [==============================] - 1s 139us/step - loss: 0.4177 - acc: 0.8211
Epoch 8/50
7200/7200 [==============================] - 1s 127us/step - loss: 0.4171 - acc: 0.8240
Epoch 9/50
7200/7200 

...

7200/7200 [==============================] - 0s 20us/step - loss: 0.3345 - acc: 0.8625
Epoch 437/500
7200/7200 [==============================] - 0s 19us/step - loss: 0.3919 - acc: 0.8382
Epoch 492/500
7200/7200 [==============================] - 0s 18us/step - loss: 0.3341 - acc: 0.8619
Epoch 438/500
7200/7200 [==============================] - 0s 18us/step - loss: 0.3917 - acc: 0.8389
Epoch 493/500
7200/7200 [==============================] - 0s 18us/step - loss: 0.3348 - acc: 0.8610
Epoch 439/500
7200/7200 [==============================] - 0s 18us/step - loss: 0.3918 - acc: 0.8390
Epoch 494/500
7200/7200 [==============================] - 0s 19us/step - loss: 0.3344 - acc: 0.8614
Epoch 440/500
7200/7200 [==============================] - 0s 18us/step - loss: 0.3916 - acc: 0.8385
Epoch 495/500
7200/7200 [==============================] - 0s 19us/step - loss: 0.3338 - acc: 0.8611
Epoch 441/500
7200/7200 [==============================] - 0s 19us/step - loss: 0.3918 - acc: 0.8376
Epoc

8000/8000 [==============================] - 0s 22us/step - loss: 0.3982 - acc: 0.8372
Epoch 90/500
8000/8000 [==============================] - 0s 22us/step - loss: 0.3979 - acc: 0.8371
Epoch 91/500
8000/8000 [==============================] - 0s 23us/step - loss: 0.3978 - acc: 0.8371
Epoch 92/500
8000/8000 [==============================] - 0s 23us/step - loss: 0.3979 - acc: 0.8386
Epoch 93/500
8000/8000 [==============================] - 0s 21us/step - loss: 0.3981 - acc: 0.8371
Epoch 94/500
8000/8000 [==============================] - 0s 22us/step - loss: 0.3978 - acc: 0.8385
Epoch 95/500
8000/8000 [==============================] - 0s 22us/step - loss: 0.3980 - acc: 0.8372
Epoch 96/500
8000/8000 [==============================] - 0s 22us/step - loss: 0.3979 - acc: 0.8370
Epoch 97/500
8000/8000 [==============================] - 0s 21us/step - loss: 0.3977 - acc: 0.8374
Epoch 98/500
8000/8000 [==============================] - 0s 23us/step - loss: 0.3975 - acc: 0.8381
Epoch 99/500


8000/8000 [==============================] - 0s 27us/step - loss: 0.3951 - acc: 0.8379
Epoch 252/500
8000/8000 [==============================] - 0s 25us/step - loss: 0.3947 - acc: 0.8384
Epoch 253/500
8000/8000 [==============================] - 0s 27us/step - loss: 0.3951 - acc: 0.8382
Epoch 254/500
8000/8000 [==============================] - 0s 24us/step - loss: 0.3951 - acc: 0.8384
Epoch 255/500
8000/8000 [==============================] - 0s 24us/step - loss: 0.3950 - acc: 0.8384
Epoch 256/500
8000/8000 [==============================] - 0s 24us/step - loss: 0.3948 - acc: 0.8394
Epoch 257/500
8000/8000 [==============================] - 0s 28us/step - loss: 0.3948 - acc: 0.8391
Epoch 258/500
8000/8000 [==============================] - 0s 27us/step - loss: 0.3949 - acc: 0.8389
Epoch 259/500
8000/8000 [==============================] - 0s 24us/step - loss: 0.3951 - acc: 0.8372
Epoch 260/500
8000/8000 [==============================] - 0s 26us/step - loss: 0.3950 - acc: 0.8385
Epoc

Epoch 332/500
8000/8000 [==============================] - 0s 29us/step - loss: 0.3948 - acc: 0.8385
Epoch 333/500
8000/8000 [==============================] - 0s 31us/step - loss: 0.3950 - acc: 0.8386
Epoch 334/500
8000/8000 [==============================] - 0s 30us/step - loss: 0.3950 - acc: 0.8374
Epoch 335/500
8000/8000 [==============================] - 0s 30us/step - loss: 0.3949 - acc: 0.8386
Epoch 336/500
8000/8000 [==============================] - 0s 29us/step - loss: 0.3949 - acc: 0.8381
Epoch 337/500
8000/8000 [==============================] - 0s 28us/step - loss: 0.3951 - acc: 0.8387
Epoch 338/500
8000/8000 [==============================] - 0s 30us/step - loss: 0.3947 - acc: 0.8400
Epoch 339/500
8000/8000 [==============================] - 0s 25us/step - loss: 0.3947 - acc: 0.8377
Epoch 340/500
8000/8000 [==============================] - 0s 25us/step - loss: 0.3949 - acc: 0.8377
Epoch 341/500
8000/8000 [==============================] - 0s 27us/step - loss: 0.3952 - ac

8000/8000 [==============================] - 0s 25us/step - loss: 0.3947 - acc: 0.8380
Epoch 414/500
8000/8000 [==============================] - 0s 25us/step - loss: 0.3946 - acc: 0.8386
Epoch 415/500
8000/8000 [==============================] - 0s 24us/step - loss: 0.3951 - acc: 0.8376
Epoch 416/500
8000/8000 [==============================] - 0s 27us/step - loss: 0.3947 - acc: 0.8389
Epoch 417/500
8000/8000 [==============================] - 0s 31us/step - loss: 0.3948 - acc: 0.8370
Epoch 418/500
8000/8000 [==============================] - 0s 26us/step - loss: 0.3948 - acc: 0.8379
Epoch 419/500
8000/8000 [==============================] - 0s 25us/step - loss: 0.3946 - acc: 0.8379
Epoch 420/500
8000/8000 [==============================] - 0s 25us/step - loss: 0.3948 - acc: 0.8382
Epoch 421/500
8000/8000 [==============================] - 0s 26us/step - loss: 0.3947 - acc: 0.8379
Epoch 422/500
8000/8000 [==============================] - 0s 25us/step - loss: 0.3947 - acc: 0.8375
Epoc

In [30]:
best_parameter=grid_search.best_params_

In [31]:
best_accuracy=grid_search.best_score_

In [32]:
best_accuracy

0.851

In [33]:
best_parameter

{'batch_size': 50, 'epochs': 500, 'optimizer': 'rmsprop'}

# End ! 